In [1]:
from vmlinux import struct_request, struct_pt_regs
from pythonbpf import bpf, section, bpfglobal, map, BPF
from pythonbpf.helper import ktime
from pythonbpf.maps import HashMap
from ctypes import c_int64, c_uint64, c_int32

REQ_WRITE = 1


@bpf
@map
def start() -> HashMap:
    return HashMap(key=c_uint64, value=c_uint64, max_entries=10240)


@bpf
@section("kprobe/blk_mq_end_request")
def trace_completion(ctx: struct_pt_regs) -> c_int64:
    # Get request pointer from first argument
    req_ptr = ctx.di
    req = struct_request(ctx.di)
    # Print: data_len, cmd_flags, latency_us
    data_len = req.__data_len
    cmd_flags = req.cmd_flags
    # Lookup start timestamp
    req_tsp = start.lookup(req_ptr)
    if req_tsp:
        # Calculate delta in nanoseconds
        delta = ktime() - req_tsp

        # Convert to microseconds for printing
        delta_us = delta // 1000

        print(f"{data_len} {cmd_flags:x} {delta_us}\n")

        # Delete the entry
        start.delete(req_ptr)

    return c_int64(0)


@bpf
@section("kprobe/blk_mq_start_request")
def trace_start(ctx1: struct_pt_regs) -> c_int32:
    req = ctx1.di
    ts = ktime()
    start.update(req, ts)
    return c_int32(0)


@bpf
@bpfglobal
def LICENSE() -> str:
    return "GPL"


b = BPF()

2025-11-25 22:47:31,621 [WARNING] pythonbpf.vmlinux_parser.class_handler: Blindly processing CFUNCTYPE ctypes to ensure compilation. Unsupported
2025-11-25 22:47:31,622 [WARNING] pythonbpf.vmlinux_parser.class_handler: Blindly processing CFUNCTYPE ctypes to ensure compilation. Unsupported
2025-11-25 22:47:31,622 [WARNING] pythonbpf.vmlinux_parser.class_handler: Blindly processing CFUNCTYPE ctypes to ensure compilation. Unsupported
2025-11-25 22:47:31,623 [WARNING] pythonbpf.vmlinux_parser.class_handler: Blindly processing CFUNCTYPE ctypes to ensure compilation. Unsupported
2025-11-25 22:47:31,623 [WARNING] pythonbpf.vmlinux_parser.class_handler: Blindly processing CFUNCTYPE ctypes to ensure compilation. Unsupported
2025-11-25 22:47:31,623 [WARNING] pythonbpf.vmlinux_parser.class_handler: Blindly processing CFUNCTYPE ctypes to ensure compilation. Unsupported
2025-11-25 22:47:31,624 [WARNING] pythonbpf.vmlinux_parser.class_handler: Blindly processing CFUNCTYPE ctypes to ensure compilatio

In [2]:
b.load()
b.attach_all()

{'trace_completion': <pylibbpf.pylibbpf.BpfProgram at 0x740702bbfcb0>,
 'trace_start': <pylibbpf.pylibbpf.BpfProgram at 0x740702bbf930>}

In [3]:
from pythonbpf import trace_pipe

In [4]:
trace_pipe()

          python-313731  [005] d.h21 204630.379933: bpf_trace_printk: 0 262146 1796


          <idle>-0       [005] d.h31 204630.380896: bpf_trace_printk: 4096 169985 657


          chrome-309323  [007] d.h21 204630.381853: bpf_trace_printk: 0 262146 625


          chrome-309323  [007] d.h31 204630.381857: bpf_trace_printk: 0 2049 668


          chrome-309323  [007] d.h31 204630.382567: bpf_trace_printk: 0 262146 618


          chrome-309323  [007] d.h41 204630.382569: bpf_trace_printk: 0 2049 645


          <idle>-0       [008] d.h31 204630.384378: bpf_trace_printk: 0 262146 651


          <idle>-0       [008] d.h31 204630.385009: bpf_trace_printk: 4096 169985 617


          chrome-309323  [007] d.h21 204630.385665: bpf_trace_printk: 0 262146 576


          chrome-309323  [007] d.h31 204630.385667: bpf_trace_printk: 0 2049 603


          chrome-309323  [007] d.h21 204630.386397: bpf_trace_printk: 0 262146 644


          chrome-309323  [007] d.h31 204630.386399: bpf_trace_pr